#### This notebook was created for the NeIC 2022 Quantum Computing Workshop held on 01.06.2022. Based on previous year notebooks.

# **Hands on! Programming a Quantum Random Number Generator**

#### Jake Muff - CSC IT Center for Science, FI

This is a real world application which is ideally suited for Quantum Computers!

## Previously...

In the preceding notebook we looked at how a **superposition state** can be created with a simple circuit using a **Hadamard** gate. Using the previous notebook as a starting point, how can we apply this to generate random numbers? 

## Task:

Using the code from the previous notebook, create a `Program()` which generates 10 random **states** and modify it to produce a random sequence of `1`'s and `0`'s. 



First import the Program, H and CNOT functions from `qat.lang.AQASM`:

In [ ]:
from XXX.XXX.XXX import XXX, XXX
from XXX.XXX import XXX

Select the Quantum Processing unit to use

In [ ]:
qpu = XXX

Allocate the qubits

In [ ]:
qbits = XXX.qalloc(XXX)

Apply the gates

In [ ]:
XXX.apply(XXX, qbits[0])

Create the circuit

In [ ]:
XXX = XXX.to_circ()

Try visualizing the circuit in the following cell:

In [ ]:
%qatdisplay XXX

Execute and display the results.
Submit the job with 10 shots. Use the hint if you are stuck!

In [ ]:
XXX = XXX.to_job(nbshots=XXX, XXX)

In [ ]:
XXX = qpu.submit(XXX)

<details>
<summary><b>Hint! Click me to reveal the hint</b></summary>
Add <code>aggregate_data=False</code> to the input of your <code>circuit.to_job</code> arguments. <p>By default the results of a job are <b>aggregated</b>. This means that if we launch measurements for example 100 times (nbshots=100), repeating outcomes are stored under one label along with the number they repeated (this is how we get and approximation for the probability of each outcome).</p> <p>It is possible to create a job without aggregating the results by using the argument <code>aggregate_data=False</code> in the to_job method. </p> <p> Try <code> job4 = circuit.to_job(nbshots=10, aggregate_data=False) </code> </p>
</details>

Print the state

In [ ]:
for sample in result:
    print("We measured the state", sample.state)

Print the state without the notation. Printing 1´s and 0´s. Use the hint!

In [ ]:
for sample in result:
    print(sample._state, end = " ") 

<details>
<summary><b>Hint! Click me to reveal the hint</b></summary>
<p> Use the underscore character '_' in front of 'state' to print without the key notation and just print the 1's and 0's. </p> <p> Include in the print statement <code> end = " " </code> to print the results in one line </p> <p> Try <code> for sample in result:
        print(sample._state, end = " ")  </code> </p>
</details>

### Solution Cell to Task 1:

In [ ]:
from qat.lang.AQASM import Program, H
from qat.pylinalg import PyLinalg

qpu = PyLinalg() 

prog = Program()

qbits = prog.qalloc(1)

prog.apply(H, qbits[0])

circuit = prog.to_circ()

# Create a job where we specify the number of shots 
# and disable the aggregation of measurement outcomes
job = circuit.to_job(nbshots=10, aggregate_data=False)

result = qpu.submit(job)

for sample in result:
    print("We measured the state", sample.state)
    
print("\n")
    
## we use the underscore '_' in front of 'state' to print without ket notation
##  and include the argument end = " " to print the results in one line
for sample in result:
    print(sample._state, end = " ")

### How do we know it's random? How random is it?

To test how good of a random number this is we can see how uniform the distribution of states is when running the program multiple times.

In [ ]:
from qat.lang.AQASM import Program, H
from qat.pylinalg import PyLinalg
import matplotlib.pyplot as plt 

qpu = PyLinalg() 

# First lets create a function for our solution

def QRNG(shots):
    prog = Program()
    qbits = prog.qalloc(1)
    prog.apply(H, qbits[0])
    circuit = prog.to_circ()
    job = circuit.to_job(nbshots=shots)
    result = qpu.submit(job)
    for sample in result:
        print("shots : ", shots, " state:", sample.state, "probability:", sample.probability)
        
    return result

# Change this to increase the number of shots
result = QRNG(1000)

states = []
y =[]

for sample in result:
    states.append(sample.state)
    y.append(sample.probability)


plt.bar([1,2], y, tick_label=states)


Seems pretty random with 1000 shots. What about more or less shots?

In [ ]:
import numpy as np

labels = []
state0_prob =[]
state1_prob =[]
for i in range(1,6):
    shots = 10**i
    labels.append(shots)
    result = QRNG(shots)
    for sample in result:
        if sample._state == 0:
            state0_prob.append(sample.probability)
        else:
            state1_prob.append(sample.probability)
            
x = np.arange(len(labels))  # the label locations
width = 0.35  # the width of the bars

fig, ax = plt.subplots(figsize=(7,7))
rects1 = ax.bar(x - width/2, state0_prob, width, label=states[0])
rects2 = ax.bar(x + width/2, state1_prob, width, label=states[1])

ax.set_ylabel('Probability')
ax.set_xticks(x, labels)
ax.legend()

ax.bar_label(rects1, padding=3)
ax.bar_label(rects2, padding=3)

fig.tight_layout()

As expected with increasing number of shots the probability equalises.

### How can we improve it?

Increasing the number of qubits? So far we've only used 1 qubit, giving us 2 possible states. If we were to use 5 qubits we would then have $2^5 = 32 $ possible states 

Below shows how the program is changed to increase the number of qubits. 

Try for yourself!

In [ ]:

prog = Program()
qbits = prog.qalloc(5)
prog.apply(H, qbits[0])
prog.apply(H, qbits[1])
prog.apply(H, qbits[2])
prog.apply(H, qbits[3])
prog.apply(H, qbits[4])
circuit = prog.to_circ()

%qatdisplay circuit

job = circuit.to_job(nbshots=5000)
result = qpu.submit(job)
i=0
#for sample in result:
#    i+=1
#    print(i," state:", sample.state, "probability:", sample.probability)
